In [0]:
%run ./utils

In [0]:
TO_SAVE: bool = False

In [0]:
survey_df = spark.read.format("csv")\
.option("header", "true")\
.option("sep", ",")\
.option("inferSchema", "true")\
.load(f's3a://{S3_RAW_PATH}2021-survey_results_public.csv').cache()

In [0]:
display(survey_df)

_c0 ResponseId MainBranch Employment Country EdLevel Age1stCode LearnCode YearsCode YearsCodePro DevType OrgSize Currency CompTotal CompFreq LanguageHaveWorkedWith LanguageWantToWorkWith DatabaseHaveWorkedWith DatabaseWantToWorkWith PlatformHaveWorkedWith PlatformWantToWorkWith WebframeHaveWorkedWith WebframeWantToWorkWith MiscTechHaveWorkedWith MiscTechWantToWorkWith ToolsTechHaveWorkedWith ToolsTechWantToWorkWith NEWCollabToolsHaveWorkedWith NEWCollabToolsWantToWorkWith OpSys NEWStuck NEWSOSites SOVisitFreq SOAccount SOPartFreq SOComm NEWOtherComms Age Gender Trans Sexuality Ethnicity Accessibility MentalHealth SurveyLength SurveyEase ConvertedCompYearly 1 1 I am a developer by profession Independent contractor, freelancer, or self-employed Slovakia Secondary school (e.g. American high school, German Realschule or Gymnasium, etc.) 18 - 24 years Coding Bootcamp;Other online resources (ex: videos, blogs, etc) NA NA Developer, mobile 20 to 99 employees EUR European Euro 4800 Monthly C++;HTML/CSS;JavaScript;Objective-C;PHP;Swift Swift PostgreSQL;SQLite SQLite NA NA Laravel;Symfony NA NA NA NA NA PHPStorm;Xcode Atom;Xcode MacOS Call a coworker or friend;Visit Stack Overflow;Go for a walk or other physical activity;Google it Stack Overflow Multiple times per day Yes A few times per month or weekly Yes, definitely No 25-34 years old Man No Straight / Heterosexual White or of European descent None of the above None of the above Appropriate in length Easy 62268 2 2 I am a student who is learning to code Student, full-time Netherlands Bachelor’s degree (B.A., B.S., B.Eng., etc.) 11 - 17 years Other online resources (ex: videos, blogs, etc);School 7 NA NA NA NA NA NA JavaScript;Python NA PostgreSQL NA NA NA Angular;Flask;Vue.js NA Cordova NA Docker;Git;Yarn Git Android Studio;IntelliJ;Notepad++;PyCharm NA Windows Visit Stack Overflow;Google it Stack Overflow Daily or almost daily Yes Daily or almost daily Yes, definitely No 18-24 years old Man No Straight / Heterosexual White or of European descent None of the above None of the above Appropriate in length Easy NA 3 3 I am not primarily a developer, but I write code sometimes as part of my work Student, full-time Russian Federation Bachelor’s degree (B.A., B.S., B.Eng., etc.) 11 - 17 years Other online resources (ex: videos, blogs, etc);Online Forum NA NA NA NA NA NA NA Assembly;C;Python;R;Rust Julia;Python;Rust SQLite SQLite Heroku NA Flask Flask NumPy;Pandas;TensorFlow;Torch/PyTorch Keras;NumPy;Pandas;TensorFlow;Torch/PyTorch NA NA IPython/Jupyter;PyCharm;RStudio;Sublime Text;Visual Studio Code IPython/Jupyter;RStudio;Sublime Text;Visual Studio Code MacOS Visit Stack Overflow;Google it;Watch help / tutorial videos;Do other work and come back later Stack Overflow;Stack Exchange Multiple times per day Yes Multiple times per day Yes, definitely Yes 18-24 years old Man No Prefer not to say Prefer not to say None of the above None of the above Appropriate in length Easy NA 4 4 I am a developer by profession Employed full-time Austria Master’s degree (M.A., M.S., M.Eng., MBA, etc.) 11 - 17 years NA NA NA Developer, front-end 100 to 499 employees EUR European Euro NA Monthly JavaScript;TypeScript JavaScript;TypeScript NA NA NA NA Angular;jQuery Angular;jQuery NA NA NA NA NA NA Windows Call a coworker or friend;Visit Stack Overflow;Go for a walk or other physical activity;Google it Stack Overflow Daily or almost daily Yes Daily or almost daily Neutral No 35-44 years old Man No Straight / Heterosexual White or of European descent I am deaf / hard of hearing NA Appropriate in length Neither easy nor difficult NA 5 5 I am a developer by profession Independent contractor, freelancer, or self-employed United Kingdom of Great Britain and Northern Ireland Master’s degree (M.A., M.S., M.Eng., MBA, etc.) 5 - 10 years Friend or family member 17 10 Developer, desktop or enterprise applications;Developer, full-stack;Engineer, data;Other (please specify): Just me - I am a freelancer, sole proprietor, etc.

In [0]:
survey_df.printSchema()

root
 |-- _c0: integer (nullable = true)
 |-- ResponseId: integer (nullable = true)
 |-- MainBranch: string (nullable = true)
 |-- Employment: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- EdLevel: string (nullable = true)
 |-- Age1stCode: string (nullable = true)
 |-- LearnCode: string (nullable = true)
 |-- YearsCode: string (nullable = true)
 |-- YearsCodePro: string (nullable = true)
 |-- DevType: string (nullable = true)
 |-- OrgSize: string (nullable = true)
 |-- Currency: string (nullable = true)
 |-- CompTotal: string (nullable = true)
 |-- CompFreq: string (nullable = true)
 |-- LanguageHaveWorkedWith: string (nullable = true)
 |-- LanguageWantToWorkWith: string (nullable = true)
 |-- DatabaseHaveWorkedWith: string (nullable = true)
 |-- DatabaseWantToWorkWith: string (nullable = true)
 |-- PlatformHaveWorkedWith: string (nullable = true)
 |-- PlatformWantToWorkWith: string (nullable = true)
 |-- WebframeHaveWorkedWith: string (nullable = true)
 |-- Webf

In [0]:
survey_df.createOrReplaceTempView('raw_survey_results')

In [0]:
total = survey_df.count()

In [0]:
print('\x1b[0;31;47m' + f'Total participants in the survey: {total}')

In [0]:
# The type of the target column - 'ConvertedCompYearly' is nullable. Let's check how many null values are.
survey_df.filter(f.col("ConvertedCompYearly").isNull()).count()

In [0]:
survey_df_with_nulls = replace_na_cols_to_null(df=survey_df)

In [0]:
display(survey_df_with_nulls)

In [0]:
# And yet we can see NA values in that column. It's 'NA' as string type and not as NoneType
# Drop column with no target value
df_with_target = survey_df.filter(f.col("ConvertedCompYearly") != 'NA')
target_count = df_with_target.count()
target_vs_all_data = target_count / total

In [0]:
print('\x1b[0;31;47m' + f'Total with no null target: {target_count}')
print('\x1b[0;31;47m' + f'Total with no null target: {target_vs_all_data: .2%}')

In [0]:
# Convert the target column - 'ConvertedCompYearly' from string type to integer
df_with_target = df_with_target.withColumn('ConvertedCompYearly', f.col('ConvertedCompYearly').cast('float'))

In [0]:
if TO_SAVE:
  save_table(df=df_with_target, file_path=f's3a://{S3_PROCESS_PATH}supervised_survey.parquet')